In [1]:
import random
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.autograd import Variable
import time
import sys

#Set device
USE_CUDA = torch.cuda.is_available()
if USE_CUDA:
    device = torch.device("cuda")
    cuda = True
else:
    device = torch.device("cpu")
    cuda = False
    
print("Device =", device)
gpus = [0]

Device = cuda


In [2]:
def time_elapsed(start_time):
    elapsed = time.time() - start_time
    hours = int(elapsed/3600)
    minutes = int(int(elapsed/60)%60)
    seconds = int(elapsed%60)
    
    return hours, minutes, seconds

In [3]:
#Load SMILES data as integer labels and as one-hot encoding
data = np.load("ohesmiles.npz")
data = data["arr_0"]

intdata = np.load("intsmiles.npz")
intdata = intdata["arr_0"]

data = torch.from_numpy(data).view(np.shape(data)[0], 1, np.shape(data)[1])
intdata = torch.from_numpy(intdata)

print("Dataset size: " + str(data.size()))
print("Integer dataset size: " + str(intdata.size()))

Dataset size: torch.Size([24825178, 1, 53])
Integer dataset size: torch.Size([24825178])


In [4]:
#Get input tensor
def inptarg(i, batch_size):
    while True:
        try:
            #Define input and target tensor sizes
            inp = torch.Tensor((seq_length - 1) * batch_size, 1, np.shape(data)[2])
            target = torch.Tensor((seq_length - 1) * batch_size)
    
            #SMILES molecules in batch 
            inputs = data[int((i * seq_length)) : int((i * seq_length) + (seq_length * batch_size)), :, :]
            targets = intdata[int((i * seq_length)) : int((i * seq_length) + (seq_length * batch_size))]

            #Index counters for input, target
            r = 0
            s = 0 
            for p in range(seq_length * batch_size - 1):
        
                if (p % seq_length != (seq_length - 1)):
                    #Input data (does not include last character in SMILES)
                    inp[r, :, :] = inputs[p, :, :]
                    r += 1
            
                if (p % seq_length != 0):
                    #Target data (does not include first character in SMILES)
                    target[s] = targets[p]
                    s += 1
                    
            return inp, target
        
        except:
            continue
        break

In [5]:
#Define model
class Model(nn.Module):
    
    #Define model parameters
    def __init__(self, input_size, hidden_size, num_layers, dropout):
        super(Model, self).__init__()
        
        #Model parameters
        self.input_size = input_size
        self.hidden_size = hidden_size
        self.num_layers = num_layers
        self.dropout = dropout
        
        #Model layers
        self.lstm = nn.LSTM(input_size = input_size, hidden_size = hidden_size, num_layers = num_layers, dropout = dropout)
        self.linear = nn.Linear(hidden_size, input_size)
        
    #Define initial hidden and cell states
    def init_states(self, num_layers, hidden_size):
        hidden = [Variable(torch.zeros(num_layers, 1, hidden_size)),
                  Variable(torch.zeros(num_layers, 1, hidden_size))]
        
        return hidden
    
    #Define forward propagation
    def forward(self, inp, hidden):
        #LSTM
        output, hidden = self.lstm(inp, hidden)

        #Linear Layer
        output = self.linear(output)
        
        return output, hidden

In [6]:
#Define training
def train():
    #Set start time
    start_time = time.time()
        
    #Iterate, looking at batch_size number of seq_length sub-sequence in each iteration
    for i in range(int((np.shape(data)[0] - seq_length + 1) / batch_size)):
            
        #Initialize hidden and cell states
        hidden = model.init_states(num_layers, hidden_size)
            
        #Run on GPU if available
        if cuda:
            hidden = (hidden[0].cuda(), hidden[1].cuda())
        
        #Set initial gradients
        model.zero_grad()
    
        #Set initial loss
        loss = 0 
            
        #Get input and target
        input_data, target_data = inptarg(i, batch_size)
        input_data = input_data.float()
        target_data = target_data.long()
            
        #Run on GPU if available
        if cuda:
            input_data = input_data.cuda()
            target_data = target_data.cuda()
                
        #Run model, calculate loss
        output, hidden = model(input_data, hidden)
        loss += criterion(output.squeeze(), target_data.squeeze())
                
        #Backpropagate loss
        loss.backward()
        optimizer.step()
            
        #Update list of losses
        if ((i % 50) == 0):
            losses[0] = loss.data.item() / seq_length   
        losses.append(loss.data.item() / seq_length)
        
        #Intermediate model saves
        if ((i % 1000) == 0):
            torch.save(model.state_dict(), "network.pth")

        #Print training info
        hours, minutes, seconds = time_elapsed(start_time)
        print("Loss: {:0.6f}".format(loss.data.item() / seq_length) + " | ΔLossTotal: {:+0.4f}".format(losses[-1] - losses[1]) + " | Iteration: {0:04d}".format(i + 1) + " | Time elapsed: {0:02d}".format(hours) + "h {0:02d}".format(minutes) + " m {0:02d}".format(seconds) + " s")

In [7]:
#Initialize model parameters
input_size = np.shape(data)[2]
hidden_size = 1024
num_layers = 3
dropout = .2
learning_rate = 0.001
seq_length = 75
batch_size = 128

#List of losses
losses = [0]

In [8]:
#Call model, set optimizer and loss function
model = Model(input_size, hidden_size, num_layers, dropout)
optimizer = torch.optim.Adam(model.parameters(), lr = learning_rate)
criterion = nn.CrossEntropyLoss()

#Run on GPU if available
if cuda:
    model.cuda()
    criterion.cuda()

In [9]:
#Total number of parameters
total_params = sum(p.numel() for p in model.parameters())
print("Total number of parameters in network: " + str(total_params))

Total number of parameters in network: 21267509


In [ ]:
#Train
train()

Loss: 0.052952 | ΔLossTotal: +0.0000 | Iteration: 0001 | Time elapsed: 00h 00 m 04 s
Loss: 0.051701 | ΔLossTotal: -0.0013 | Iteration: 0002 | Time elapsed: 00h 00 m 08 s
Loss: 0.044027 | ΔLossTotal: -0.0089 | Iteration: 0003 | Time elapsed: 00h 00 m 12 s
Loss: 0.046113 | ΔLossTotal: -0.0068 | Iteration: 0004 | Time elapsed: 00h 00 m 17 s
Loss: 0.038127 | ΔLossTotal: -0.0148 | Iteration: 0005 | Time elapsed: 00h 00 m 21 s
Loss: 0.038344 | ΔLossTotal: -0.0146 | Iteration: 0006 | Time elapsed: 00h 00 m 25 s
Loss: 0.038744 | ΔLossTotal: -0.0142 | Iteration: 0007 | Time elapsed: 00h 00 m 29 s
Loss: 0.038082 | ΔLossTotal: -0.0149 | Iteration: 0008 | Time elapsed: 00h 00 m 33 s
Loss: 0.037230 | ΔLossTotal: -0.0157 | Iteration: 0009 | Time elapsed: 00h 00 m 37 s
Loss: 0.036599 | ΔLossTotal: -0.0164 | Iteration: 0010 | Time elapsed: 00h 00 m 41 s
Loss: 0.036342 | ΔLossTotal: -0.0166 | Iteration: 0011 | Time elapsed: 00h 00 m 45 s
Loss: 0.036429 | ΔLossTotal: -0.0165 | Iteration: 0012 | Time ela

Loss: 0.034986 | ΔLossTotal: -0.0180 | Iteration: 0098 | Time elapsed: 00h 06 m 43 s
Loss: 0.034333 | ΔLossTotal: -0.0186 | Iteration: 0099 | Time elapsed: 00h 06 m 47 s
Loss: 0.034574 | ΔLossTotal: -0.0184 | Iteration: 0100 | Time elapsed: 00h 06 m 52 s
Loss: 0.034330 | ΔLossTotal: -0.0186 | Iteration: 0101 | Time elapsed: 00h 06 m 56 s
Loss: 0.034040 | ΔLossTotal: -0.0189 | Iteration: 0102 | Time elapsed: 00h 07 m 00 s
Loss: 0.034041 | ΔLossTotal: -0.0189 | Iteration: 0103 | Time elapsed: 00h 07 m 04 s
Loss: 0.033679 | ΔLossTotal: -0.0193 | Iteration: 0104 | Time elapsed: 00h 07 m 08 s
Loss: 0.033729 | ΔLossTotal: -0.0192 | Iteration: 0105 | Time elapsed: 00h 07 m 12 s
Loss: 0.033511 | ΔLossTotal: -0.0194 | Iteration: 0106 | Time elapsed: 00h 07 m 16 s
Loss: 0.033227 | ΔLossTotal: -0.0197 | Iteration: 0107 | Time elapsed: 00h 07 m 21 s
Loss: 0.033211 | ΔLossTotal: -0.0197 | Iteration: 0108 | Time elapsed: 00h 07 m 25 s
Loss: 0.033014 | ΔLossTotal: -0.0199 | Iteration: 0109 | Time ela

Loss: 0.035988 | ΔLossTotal: -0.0170 | Iteration: 0195 | Time elapsed: 00h 13 m 25 s
Loss: 0.021953 | ΔLossTotal: -0.0310 | Iteration: 0196 | Time elapsed: 00h 13 m 29 s
Loss: 0.021907 | ΔLossTotal: -0.0310 | Iteration: 0197 | Time elapsed: 00h 13 m 33 s
Loss: 0.021772 | ΔLossTotal: -0.0312 | Iteration: 0198 | Time elapsed: 00h 13 m 37 s
Loss: 0.021679 | ΔLossTotal: -0.0313 | Iteration: 0199 | Time elapsed: 00h 13 m 42 s
Loss: 0.021627 | ΔLossTotal: -0.0313 | Iteration: 0200 | Time elapsed: 00h 13 m 46 s
Loss: 0.021534 | ΔLossTotal: -0.0314 | Iteration: 0201 | Time elapsed: 00h 13 m 50 s
Loss: 0.021411 | ΔLossTotal: -0.0315 | Iteration: 0202 | Time elapsed: 00h 13 m 54 s
Loss: 0.021318 | ΔLossTotal: -0.0316 | Iteration: 0203 | Time elapsed: 00h 13 m 58 s
Loss: 0.021263 | ΔLossTotal: -0.0317 | Iteration: 0204 | Time elapsed: 00h 14 m 02 s
Loss: 0.021343 | ΔLossTotal: -0.0316 | Iteration: 0205 | Time elapsed: 00h 14 m 06 s
Loss: 0.021609 | ΔLossTotal: -0.0313 | Iteration: 0206 | Time ela

Loss: 0.015925 | ΔLossTotal: -0.0370 | Iteration: 0292 | Time elapsed: 00h 20 m 07 s
Loss: 0.015823 | ΔLossTotal: -0.0371 | Iteration: 0293 | Time elapsed: 00h 20 m 11 s
Loss: 0.015637 | ΔLossTotal: -0.0373 | Iteration: 0294 | Time elapsed: 00h 20 m 16 s
Loss: 0.015694 | ΔLossTotal: -0.0373 | Iteration: 0295 | Time elapsed: 00h 20 m 20 s
Loss: 0.015547 | ΔLossTotal: -0.0374 | Iteration: 0296 | Time elapsed: 00h 20 m 24 s
Loss: 0.015610 | ΔLossTotal: -0.0373 | Iteration: 0297 | Time elapsed: 00h 20 m 28 s
Loss: 0.015424 | ΔLossTotal: -0.0375 | Iteration: 0298 | Time elapsed: 00h 20 m 32 s
Loss: 0.015465 | ΔLossTotal: -0.0375 | Iteration: 0299 | Time elapsed: 00h 20 m 37 s
Loss: 0.015325 | ΔLossTotal: -0.0376 | Iteration: 0300 | Time elapsed: 00h 20 m 41 s
Loss: 0.015394 | ΔLossTotal: -0.0376 | Iteration: 0301 | Time elapsed: 00h 20 m 45 s
Loss: 0.015251 | ΔLossTotal: -0.0377 | Iteration: 0302 | Time elapsed: 00h 20 m 49 s
Loss: 0.015217 | ΔLossTotal: -0.0377 | Iteration: 0303 | Time ela

Loss: 0.009926 | ΔLossTotal: -0.0430 | Iteration: 0389 | Time elapsed: 00h 26 m 50 s
Loss: 0.009554 | ΔLossTotal: -0.0434 | Iteration: 0390 | Time elapsed: 00h 26 m 54 s
Loss: 0.009590 | ΔLossTotal: -0.0434 | Iteration: 0391 | Time elapsed: 00h 26 m 59 s
Loss: 0.009393 | ΔLossTotal: -0.0436 | Iteration: 0392 | Time elapsed: 00h 27 m 03 s
Loss: 0.009192 | ΔLossTotal: -0.0438 | Iteration: 0393 | Time elapsed: 00h 27 m 07 s
Loss: 0.009054 | ΔLossTotal: -0.0439 | Iteration: 0394 | Time elapsed: 00h 27 m 11 s
Loss: 0.038267 | ΔLossTotal: -0.0147 | Iteration: 0395 | Time elapsed: 00h 27 m 15 s
Loss: 0.009586 | ΔLossTotal: -0.0434 | Iteration: 0396 | Time elapsed: 00h 27 m 19 s
Loss: 0.008927 | ΔLossTotal: -0.0440 | Iteration: 0397 | Time elapsed: 00h 27 m 23 s
Loss: 0.009190 | ΔLossTotal: -0.0438 | Iteration: 0398 | Time elapsed: 00h 27 m 28 s
Loss: 0.008932 | ΔLossTotal: -0.0440 | Iteration: 0399 | Time elapsed: 00h 27 m 32 s
Loss: 0.008801 | ΔLossTotal: -0.0442 | Iteration: 0400 | Time ela

...

Loss: 0.001153 | ΔLossTotal: -0.0518 | Iteration: 50408 | Time elapsed: 58h 47 m 59 s
Loss: 0.001208 | ΔLossTotal: -0.0517 | Iteration: 50409 | Time elapsed: 58h 48 m 03 s
Loss: 0.001162 | ΔLossTotal: -0.0518 | Iteration: 50410 | Time elapsed: 58h 48 m 07 s
Loss: 0.001169 | ΔLossTotal: -0.0518 | Iteration: 50411 | Time elapsed: 58h 48 m 12 s
Loss: 0.001112 | ΔLossTotal: -0.0518 | Iteration: 50412 | Time elapsed: 58h 48 m 16 s
Loss: 0.001139 | ΔLossTotal: -0.0518 | Iteration: 50413 | Time elapsed: 58h 48 m 20 s
Loss: 0.001075 | ΔLossTotal: -0.0519 | Iteration: 50414 | Time elapsed: 58h 48 m 24 s
Loss: 0.001106 | ΔLossTotal: -0.0518 | Iteration: 50415 | Time elapsed: 58h 48 m 28 s
Loss: 0.001158 | ΔLossTotal: -0.0518 | Iteration: 50416 | Time elapsed: 58h 48 m 32 s
Loss: 0.001112 | ΔLossTotal: -0.0518 | Iteration: 50417 | Time elapsed: 58h 48 m 37 s
Loss: 0.001081 | ΔLossTotal: -0.0519 | Iteration: 50418 | Time elapsed: 58h 48 m 41 s
Loss: 0.001099 | ΔLossTotal: -0.0519 | Iteration: 5041

Loss: 0.001027 | ΔLossTotal: -0.0519 | Iteration: 50504 | Time elapsed: 58h 56 m 33 s
Loss: 0.001029 | ΔLossTotal: -0.0519 | Iteration: 50505 | Time elapsed: 58h 56 m 37 s
Loss: 0.001044 | ΔLossTotal: -0.0519 | Iteration: 50506 | Time elapsed: 58h 56 m 41 s
Loss: 0.001070 | ΔLossTotal: -0.0519 | Iteration: 50507 | Time elapsed: 58h 56 m 46 s
Loss: 0.001141 | ΔLossTotal: -0.0518 | Iteration: 50508 | Time elapsed: 58h 56 m 50 s
Loss: 0.000967 | ΔLossTotal: -0.0520 | Iteration: 50509 | Time elapsed: 58h 56 m 54 s
Loss: 0.001127 | ΔLossTotal: -0.0518 | Iteration: 50510 | Time elapsed: 58h 56 m 58 s
Loss: 0.000977 | ΔLossTotal: -0.0520 | Iteration: 50511 | Time elapsed: 58h 57 m 03 s
Loss: 0.000963 | ΔLossTotal: -0.0520 | Iteration: 50512 | Time elapsed: 58h 57 m 07 s
Loss: 0.000995 | ΔLossTotal: -0.0520 | Iteration: 50513 | Time elapsed: 58h 57 m 11 s
Loss: 0.000947 | ΔLossTotal: -0.0520 | Iteration: 50514 | Time elapsed: 58h 57 m 15 s
Loss: 0.001030 | ΔLossTotal: -0.0519 | Iteration: 5051

Loss: 0.000952 | ΔLossTotal: -0.0520 | Iteration: 50600 | Time elapsed: 59h 05 m 08 s
Loss: 0.001021 | ΔLossTotal: -0.0519 | Iteration: 50601 | Time elapsed: 59h 05 m 15 s
Loss: 0.001046 | ΔLossTotal: -0.0519 | Iteration: 50602 | Time elapsed: 59h 05 m 22 s
Loss: 0.001056 | ΔLossTotal: -0.0519 | Iteration: 50603 | Time elapsed: 59h 05 m 28 s
Loss: 0.001023 | ΔLossTotal: -0.0519 | Iteration: 50604 | Time elapsed: 59h 05 m 32 s
Loss: 0.001006 | ΔLossTotal: -0.0519 | Iteration: 50605 | Time elapsed: 59h 05 m 37 s
Loss: 0.000999 | ΔLossTotal: -0.0520 | Iteration: 50606 | Time elapsed: 59h 05 m 41 s
Loss: 0.001039 | ΔLossTotal: -0.0519 | Iteration: 50607 | Time elapsed: 59h 05 m 45 s
Loss: 0.001052 | ΔLossTotal: -0.0519 | Iteration: 50608 | Time elapsed: 59h 05 m 50 s
Loss: 0.001067 | ΔLossTotal: -0.0519 | Iteration: 50609 | Time elapsed: 59h 05 m 54 s
Loss: 0.001068 | ΔLossTotal: -0.0519 | Iteration: 50610 | Time elapsed: 59h 05 m 58 s
Loss: 0.001103 | ΔLossTotal: -0.0518 | Iteration: 5061

Loss: 0.000919 | ΔLossTotal: -0.0520 | Iteration: 50696 | Time elapsed: 59h 12 m 10 s
Loss: 0.000929 | ΔLossTotal: -0.0520 | Iteration: 50697 | Time elapsed: 59h 12 m 14 s
Loss: 0.000889 | ΔLossTotal: -0.0521 | Iteration: 50698 | Time elapsed: 59h 12 m 18 s
Loss: 0.000927 | ΔLossTotal: -0.0520 | Iteration: 50699 | Time elapsed: 59h 12 m 23 s
Loss: 0.000943 | ΔLossTotal: -0.0520 | Iteration: 50700 | Time elapsed: 59h 12 m 27 s
Loss: 0.000988 | ΔLossTotal: -0.0520 | Iteration: 50701 | Time elapsed: 59h 12 m 31 s
Loss: 0.000944 | ΔLossTotal: -0.0520 | Iteration: 50702 | Time elapsed: 59h 12 m 36 s
Loss: 0.001013 | ΔLossTotal: -0.0519 | Iteration: 50703 | Time elapsed: 59h 12 m 40 s
Loss: 0.000981 | ΔLossTotal: -0.0520 | Iteration: 50704 | Time elapsed: 59h 12 m 44 s
Loss: 0.000976 | ΔLossTotal: -0.0520 | Iteration: 50705 | Time elapsed: 59h 12 m 49 s
Loss: 0.001013 | ΔLossTotal: -0.0519 | Iteration: 50706 | Time elapsed: 59h 12 m 53 s
Loss: 0.001032 | ΔLossTotal: -0.0519 | Iteration: 5070

Loss: 0.001193 | ΔLossTotal: -0.0518 | Iteration: 50792 | Time elapsed: 59h 19 m 32 s
Loss: 0.001190 | ΔLossTotal: -0.0518 | Iteration: 50793 | Time elapsed: 59h 19 m 39 s
Loss: 0.001180 | ΔLossTotal: -0.0518 | Iteration: 50794 | Time elapsed: 59h 19 m 45 s
Loss: 0.001101 | ΔLossTotal: -0.0519 | Iteration: 50795 | Time elapsed: 59h 19 m 52 s
Loss: 0.001136 | ΔLossTotal: -0.0518 | Iteration: 50796 | Time elapsed: 59h 19 m 59 s
Loss: 0.001223 | ΔLossTotal: -0.0517 | Iteration: 50797 | Time elapsed: 59h 20 m 05 s
Loss: 0.001175 | ΔLossTotal: -0.0518 | Iteration: 50798 | Time elapsed: 59h 20 m 12 s
Loss: 0.001202 | ΔLossTotal: -0.0518 | Iteration: 50799 | Time elapsed: 59h 20 m 18 s
Loss: 0.001143 | ΔLossTotal: -0.0518 | Iteration: 50800 | Time elapsed: 59h 20 m 25 s
Loss: 0.001110 | ΔLossTotal: -0.0518 | Iteration: 50801 | Time elapsed: 59h 20 m 31 s
Loss: 0.001144 | ΔLossTotal: -0.0518 | Iteration: 50802 | Time elapsed: 59h 20 m 38 s
Loss: 0.001093 | ΔLossTotal: -0.0519 | Iteration: 5080

In [ ]:
torch.save(model.state_dict(), "network.pth")

In [ ]:
with open('losses.txt', 'w') as f:
    for item in losses:
        f.write("%s\n" % item)